In [12]:
import ee
import json

In [13]:
ee.Initialize(project = 'usfs-carbon-viz-test')

In [14]:
image_asset_id = 'projects/usfs-carbon-viz-test/assets/Carbon_Emissions/Carbon_Emissions_tile2'
image = ee.Image(image_asset_id)

In [15]:
states = ee.FeatureCollection("TIGER/2018/States")
louisiana = states.filter(ee.Filter.eq('STATEFP', '22')).first()

counties = ee.FeatureCollection("TIGER/2018/Counties")
louisiana_county = counties.filter(ee.Filter.eq('STATEFP', '22')).first()

scale = 30  

In [16]:
# def compute_band_stats(image, boundary_geometry):
#     """
#     Compute summary statistics for each band within the specified boundary from an Image.

#     Args:
#         image (ee.Image): The input Image to analyze.
#         boundary_geometry (ee.Geometry): The boundary geometry uploaded by the user.

#     Returns:
#         str: A JSON string with computed statistics for each band.
#     """
#     # Initialize an empty dictionary to hold statistics for all bands.
#     stats_dict = {}

#     # Get the list of bands from the image.
#     bands = image.bandNames().getInfo()

#     # Iterate over each band in the image.
#     for band in bands:
#         band_image = image.select(band)

#         # Reduce the image within the boundary geometry.
#         stats = band_image.reduceRegion(
#             reducer=ee.Reducer.mean()
#             .combine(reducer2=ee.Reducer.min(), sharedInputs=True)
#             .combine(reducer2=ee.Reducer.max(), sharedInputs=True)
#             .combine(reducer2=ee.Reducer.sum(), sharedInputs=True)
#             .combine(reducer2=ee.Reducer.median(), sharedInputs=True)
#             .combine(reducer2=ee.Reducer.stdDev(), sharedInputs=True),
#             geometry=boundary_geometry,
#             scale=30,
#             bestEffort=True
#         )

#         # Fetch and format the results for this band.
#         stats = stats.getInfo()
#         stats_dict[band] = {
#             "mean": stats.get(f"{band}_mean"),
#             "min": stats.get(f"{band}_min"),
#             "max": stats.get(f"{band}_max"),
#             "sum": stats.get(f"{band}_sum"),
#             "median": stats.get(f"{band}_median"),
#             "stdDev": stats.get(f"{band}_stdDev"),
#         }

#     # Convert the dictionary to a JSON string.
#     # stats_json = json.dumps(stats_dict)
#     return stats_dict

In [27]:
def compute_band_stats(image, boundary_geometry):
    """
    Compute summary statistics for each band within the specified boundary from an Image.

    Args:
        image (ee.Image): The input Image to analyze.
        boundary_geometry (ee.Geometry): The boundary geometry uploaded by the user.

    Returns:
        ee.FeatureCollection: A FeatureCollection with computed statistics for each band.
    """
    # Initialize an empty list to hold features.
    features = []

    # Get the list of bands from the image.
    bands = image.bandNames().getInfo()

    # Iterate over each band in the image.
    for band in bands:
        band_image = image.select(band)

        # Reduce the image within the boundary geometry.
        stats = band_image.reduceRegion(
            reducer=ee.Reducer.mean()
            .combine(reducer2=ee.Reducer.min(), sharedInputs=True)
            .combine(reducer2=ee.Reducer.max(), sharedInputs=True)
            .combine(reducer2=ee.Reducer.sum(), sharedInputs=True)
            .combine(reducer2=ee.Reducer.median(), sharedInputs=True)
            .combine(reducer2=ee.Reducer.stdDev(), sharedInputs=True),
            geometry=boundary_geometry,
            scale=30,
            bestEffort=True
        )

        # Check if each statistic is present before adding it to the feature
        stats_dict = {
            f"{band}_mean": stats.get(f"{band}_mean"),
            f"{band}_min": stats.get(f"{band}_min"),
            f"{band}_max": stats.get(f"{band}_max"),
            f"{band}_sum": stats.get(f"{band}_sum", ee.Number(0)),  # Default to 0 if not present
            f"{band}_median": stats.get(f"{band}_median", ee.Number(0)),  # Default to 0 if not present
            f"{band}_stdDev": stats.get(f"{band}_stdDev", ee.Number(0)),  # Default to 0 if not present
        }

        # Create a feature for this band with stats as properties.
        feature = ee.Feature(boundary_geometry, stats_dict)
        features.append(feature)

    # Return all features as a FeatureCollection.
    return ee.FeatureCollection(features)

In [33]:
ee.data.setDefaultWorkloadTag('usfs-online-compute');
ee.data.setWorkloadTag('usfs-batch-online');

In [34]:
computed_stats = compute_band_stats(image, louisiana.geometry())
print(computed_stats.getInfo())

{'type': 'FeatureCollection', 'columns': {'system:index': 'String'}, 'features': [{'type': 'Feature', 'geometry': {'type': 'GeometryCollection', 'geometries': [{'type': 'LineString', 'coordinates': [[-93.73116346407087, 30.0894875369958], [-93.73107369749323, 30.08953242028464]]}, {'type': 'Polygon', 'coordinates': [[[-94.04337163374153, 32.52211688047716], [-94.04319206071573, 32.51794277891147], [-94.04328184715106, 32.51677581821639], [-94.043236953914, 32.51619227927312], [-94.043236953914, 32.51605764869314], [-94.04310235237489, 32.51426235930292], [-94.04292278027947, 32.51358908384868], [-94.04301256624963, 32.51282606623931], [-94.04301256624963, 32.51264652419651], [-94.04301256624963, 32.51224261811502], [-94.04301256624963, 32.51215280353246], [-94.04305745929288, 32.51179374394389], [-94.04314716755621, 32.510716533194696], [-94.04314716755621, 32.50972915754905], [-94.04314716755621, 32.508966143790964], [-94.04314716755621, 32.50878659511909], [-94.04310235237489, 32.508

In [37]:
ee.data.setDefaultWorkloadTag('usfs-batch-compute');
ee.data.setWorkloadTag('usfs-batch-export');

In [20]:
export_image = ee.batch.Export.image.toAsset(
    image=image,
    description="export_boundary_louisiana",
    assetId= 'projects/usfs-carbon-viz-test/assets/test/test_lousiana_county',
    region=louisiana.geometry(),
    scale=scale,
    maxPixels=1e13
)
export_image.start()
print("Started export task")

Started export task


In [38]:
export_table = ee.batch.Export.table.toAsset(
    collection=computed_stats,
    description='export_louisiana_test',
    assetId= 'projects/usfs-carbon-viz-test/assets/test/test_lousiana_stats'
)
export_table.start()

In [ ]:
#Table export
#Lousiana usage for computing stats of all bands (7 total)
# batch - 0.1077 EECU seconds ($0.40/EECU hour)(0.0000299 EECU hours = $0.00001196)

#Lousiana county usage for computing stats of all bands 
# batch - 0.0633 EECU seconds 

#Image export
#Lousiana usage for batch exporting all bands (7 total)
# batch - 2164.1025 EECU seconds ($0.40/EECU hour)(0.6011 hours = $0.24)

#Lousiana county usage for batch exporting all bands
# batch - 4.4618 EECU seconds